In [1]:
import re
import numpy as np

In [65]:
pkt_nr_rx = re.compile("##### PA_LFR_PKT_NR_ASM: (\d) #####")
start_rx = re.compile("##### Seconds : .*")
end_rx = re.compile("##### SOURCE DATA BEGIN - Offset in the file \(byte pos\): \d+ #####")

def pkt_nr(line):
    m=pkt_nr_rx.match(line)
    return m.groups()[0] if m else None

def is_data(line):
    return line[0]==' '

def is_data_start(line):
    m=start_rx.match(line)
    return bool(m)

def is_data_end(line):
    m=end_rx.match(line)
    return bool(m)

def load_asm(fname):
    ASMs=[]
    lines=open(fname,"r").readlines()
    pkts_nr = list(map(int,filter(lambda v: v is not None, (map(pkt_nr ,lines)))))
    assert np.all(np.sum(np.gradient(np.array(pkts_nr).reshape((-1, 3)), axis=0), axis=0)==0)
    datas = list(map(is_data_start,lines))
    datae = list(map(is_data_end,lines))
    start_offsets = np.arange(len(datas))[datas]+1
    end_offsets = np.append((np.arange(len(datae))[datae])[1:],[len(lines)])
    
    matrices_data_indexes=np.array(list(zip(start_offsets, end_offsets))).reshape(-1,3,2)
    data_array=np.array(lines)

    for asm_idx in matrices_data_indexes:
        str_data = ''.join(data_array[asm_idx[0][0]:asm_idx[0][1]])+ ''.join(data_array[asm_idx[1][0]:asm_idx[1][1]])+''.join(data_array[asm_idx[2][0]:asm_idx[2][1]])
        values = list(map(float, str_data.replace('\n','').strip().split()))
        ASMs+=values
    return np.array(ASMs).reshape(matrices_data_indexes.shape[0],-1,25)

In [66]:
ASM_F0=load_asm('2022_03_17_13_10_24_packet_record_NORMAL.af0')

In [67]:
ASM_F1=load_asm('2022_03_17_13_10_24_packet_record_NORMAL.af1')

In [68]:
ASM_F2=load_asm('2022_03_17_13_10_24_packet_record_NORMAL.af2')

In [75]:
np.unravel_index(np.argmax(ASM_F1, axis=None),ASM_F1.shape)

(1, 51, 0)

In [78]:
ASM_F1[:,np.unravel_index(np.argmax(ASM_F1, axis=None),ASM_F1.shape)[1],:]

array([[1.5468750e+00, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 7.1875000e-01, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        7.3437500e-01, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 8.1250000e-01, 0.0000000e+00, 0.0000000e+00,
        7.9687500e-01],
       [2.0753868e+07, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 2.0575776e+07, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        2.0704210e+07, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 2.0396636e+07, 0.0000000e+00, 0.0000000e+00,
        2.0595084e+07],
       [2.0750388e+07, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,
        0.0000000e+00, 0.0000000e+00, 0.0000000e+00, 0.0000000e+00,


In [79]:
ASM_F2[:,np.unravel_index(np.argmax(ASM_F2, axis=None),ASM_F2.shape)[1],:]

array([[ 1.  ,  0.  ,  0.  ,  0.25,  0.  ,  0.25,  0.  ,  0.5 , -0.5 ,
         0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.5 ,  0.5 ,
         0.  ,  0.  , -0.5 ,  0.5 ,  0.  , -0.5 ,  1.  ],
       [ 0.5 ,  0.  ,  0.  ,  0.5 ,  0.  ,  0.  ,  0.  ,  0.  , -0.25,
         0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  1.25,  0.  ,
         0.  ,  0.25, -0.5 ,  0.  ,  0.  ,  0.  ,  0.5 ],
       [ 1.75,  0.  , -0.25,  1.  , -0.25,  0.  , -0.25, -0.25, -0.75,
         0.25,  0.  ,  0.25,  0.  ,  0.  ,  0.  ,  0.  ,  0.75,  0.  ,
        -0.25,  0.  , -0.5 ,  0.5 ,  0.25,  0.  ,  0.5 ],
       [ 3.25,  0.25,  0.25,  1.25, -0.5 ,  0.  ,  0.  ,  0.  ,  0.  ,
         0.25,  0.25,  0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  1.  ,  0.  ,
         0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.  ],
       [ 2.  ,  0.5 , -0.25,  0.  , -0.75,  0.  , -0.25, -0.25, -0.5 ,
         0.25,  0.  , -0.25,  0.  ,  0.  ,  0.  ,  0.  ,  0.5 ,  0.  ,
         0.  ,  0.  , -0.25,  0.25,  0.25,  0.  ,  0.5 ],


In [80]:
ASM_F0[:,np.unravel_index(np.argmax(ASM_F0, axis=None),ASM_F0.shape)[1],:]

array([[ 6.64062500e-01,  4.16666657e-01,  1.30208330e-02,
         2.29166672e-01, -3.38541679e-02,  3.80208343e-01,
         1.27604172e-01,  4.01041657e-01,  8.33333358e-02,
         1.43489587e+00,  4.01041657e-01, -5.20833321e-02,
         7.96875000e-01,  1.43229172e-01,  6.69270813e-01,
         1.19791664e-01,  7.47395813e-01,  4.21875000e-01,
         1.53645828e-01,  4.45312500e-01,  1.38020828e-01,
         1.67447913e+00,  7.31770813e-01, -4.16666679e-02,
         1.41145837e+00],
       [ 1.60859375e+01,  1.49921875e+01,  7.65625000e-01,
         1.34375000e+01,  3.02604175e+00,  1.39765625e+01,
         3.27604175e+00,  1.33697920e+01,  3.66666675e+00,
         1.58411455e+01,  1.30755205e+01,  2.23958325e+00,
         1.37604170e+01,  2.45312500e+00,  1.32838545e+01,
         2.87500000e+00,  1.34791670e+01,  1.30026045e+01,
         9.89583358e-02,  1.26796875e+01,  4.92187500e-01,
         1.52786455e+01,  1.30208330e+01,  3.54166657e-01,
         1.44947920e+01],
    